In [11]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

from iterstrat.ml_stratifiers import MultilabelStratifiedKFold # pip3 install --user iterative-stratification on SCC
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV, StratifiedKFold
from sklearn.metrics import confusion_matrix

import random
import math
from collections import Counter

In [2]:
df=pd.read_csv('../Data/20221212-pheno_mat_select_red-builds_acid_from.tsv', sep='\t' ,index_col='id')  # ,index_col='strain',index_col='Mutant'
print('df.shape',df.shape)
df=df.drop(df[(df.std(axis=1)==0)].index)
print('df.shape',df.shape)
n_unique=[]
for c in df.columns:
    n_unique.append((c,df[c].nunique()))
df_n_unique=pd.DataFrame(n_unique, columns=['col','nunique'])    
print(df_n_unique['nunique'].value_counts())
df=df[df_n_unique.query("nunique==2")['col'].values]
print('df.shape',df.shape)
df=df.drop(df[(df.std(axis=1)==0)].index)
print('df.shape',df.shape)
df.head()

df.shape (637, 46)
df.shape (636, 46)
nunique
2    46
Name: count, dtype: int64
df.shape (636, 46)
df.shape (636, 46)


MU:galactitol_builds acid from  MU:glycerol_builds acid from   
id                                                                  
416                               0                             0  \
572                               0                             0   
683                               0                             0   
628                               0                             0   
599                               0                             0   

     MU:lactose_builds acid from  MU:maltose_builds acid from   
id                                                              
416                            0                            0  \
572                            0                            0   
683                            0                            0   
628                            0                            2   
599                            0                            2   

     MU:sucrose_builds acid from  MU:amygdalin_builds acid from   
id                                                                
416                            0                              0  \
572                            0                              0   
683                            0                              0   
628                            2                              0   
599                            0                              0   

     MU:arbutin_builds acid from  MU:cellobiose_builds acid from   
id                                                                 
416                            0                               0  \
572                            0                               0   
683                            0                               0   
628                            2                               2   
599                            0                               0   

     MU:D-arabinose_builds acid from  MU:D-arabitol_builds acid from  ...   
id                                                                    ...   
416                                0                               0  ...  \
572                                0                               0  ...   
683                                0                               0  ...   
628                                0                               0  ...   
599                                0                               0  ...   

     MU:methyl beta-D-xylopyranoside_builds acid from   
id                                                      
416                                                 0  \
572                                                 0   
683                                                 0   
628                                                 0   
599                                                 0   

     MU:myo-inositol_builds acid from   
id                                      
416                                 0  \
572                                 0   
683                                 0   
628                                 0   
599                                 0   

     MU:N-acetylglucosamine_builds acid from  MU:raffinose_builds acid from   
id                                                                            
416                                        0                              0  \
572                                        0                              0   
683                                        0                              0   
628                                        2                              0   
599                                        0                              0   

     MU:ribitol_builds acid from  MU:turanose_builds acid from   
id                                                               
416                            0                             0  \
572                            0                             0   
683                            0                             2   
628   

In [3]:
df.std(axis=1)

id
416       0.499275
572       0.412369
683       0.412369
628       0.862532
599       0.412369
            ...   
160084    0.910486
160083    0.930430
160082    0.930430
160081    0.887922
160364    0.930430
Length: 636, dtype: float64

In [4]:
df_new=df.replace(2,1)
X=df_new.values
n, d = X.shape
print((n, d))

(636, 46)


In [5]:
X[X==0]=-1
print(X.dtype)##dtype('int64') 
X

int64


array([[-1, -1, -1, ..., -1, -1,  1],
       [-1, -1, -1, ..., -1, -1,  1],
       [-1, -1, -1, ..., -1, -1, -1],
       ...,
       [-1, -1, -1, ..., -1, -1, -1],
       [-1, -1, -1, ..., -1, -1, -1],
       [-1, -1,  1, ..., -1, -1, -1]])

## Random Forest classifier

In [6]:
df_z_all=pd.read_csv('../Results/bacdive1_MIP_classify_z_all.csv')
df_z_all.head()

MU:galactitol_builds acid from  MU:glycerol_builds acid from   
0                               0                             1  \
1                               0                             1   
2                               0                             1   
3                               0                             1   
4                               1                             1   

   MU:lactose_builds acid from  MU:maltose_builds acid from   
0                            1                            1  \
1                            1                            1   
2                            1                            1   
3                            1                            1   
4                            1                            1   

   MU:sucrose_builds acid from  MU:amygdalin_builds acid from   
0                            1                              1  \
1                            1                              1   
2                            1                              1   
3                            1                              1   
4                            1                              1   

   MU:arbutin_builds acid from  MU:cellobiose_builds acid from   
0                            1                               1  \
1                            1                               1   
2                            1                               1   
3                            1                               1   
4                            1                               1   

   MU:D-arabinose_builds acid from  MU:D-arabitol_builds acid from  ...   
0                                1                               1  ...  \
1                                1                               1  ...   
2                                1                               1  ...   
3                                1                               1  ...   
4                                1                               1  ...   

   MU:methyl beta-D-xylopyranoside_builds acid from   
0                                                 1  \
1                                                 1   
2                                                 1   
3                                                 1   
4                                                 1   

   MU:myo-inositol_builds acid from  MU:N-acetylglucosamine_builds acid from   
0                                 1                                        1  \
1                                 1                                        1   
2                                 1                                        1   
3                                 1                                        1   
4                                 1                                        1   

   MU:raffinose_builds acid from  MU:ribitol_builds acid from   
0                              1                            1  \
1                              1                            1   
2                              1                            1   
3                              1                            1   
4                              1                            1   

   MU:turanose_builds acid from  MU:xylitol_builds acid from   
0                             1                            1  \
1                             1                            1   
2                             1                            0   
3                             1                            0   
4                             1                            0   

   MU:trehalose_builds acid from   
0                              1  \
1                              1   
2                              1   
3                              1   
4                              1   

   MU:Potassium 2-ketogluconate_builds acid from   
0                                              1  \
1                                              1   
2                    

In [12]:
df_z_all.shape

(45, 46)

In [13]:
names_raw=df.columns.values
n, d = X.shape  

z_last = df_z_all.iloc[-1,:].values
y_last = X[:,z_last==0] 


myseed = 2020
cvFolds= 5

In [9]:
def sample_attrs(attrs, r, max=100, seed = 1234567890):
    i = 0
    random.seed(seed)
    while i < max:
        preds = random.sample(attrs, r)
        preds.sort()
        resps = list(set(attrs) - set(preds))
        yield (preds, resps)
        i += 1

In [10]:
def entropy(data):
    l = len(data)
    if l <= 1:
        return 0
    counts = Counter()
    for d in data:
        counts[d] += 1
    ent = 0
    probs = [float(c) / len(data) for c in counts.values()]
    for p in probs:
        ent -= p * math.log(p, 2.)
    return ent

x_idxs_byentropy = df.apply(entropy, 0).reset_index().sort_values(0, ascending=False)
x_idxs_byentropy = list(x_idxs_byentropy.index)

In [14]:
from sklearn.metrics import accuracy_score, balanced_accuracy_score, f1_score, jaccard_score, cohen_kappa_score, matthews_corrcoef

stats_all=[]
acc_all=[]
b_acc_all=[]
f1_weight_all=[]
jaccard_all=[]
cohen_kappa_all=[]
mcc_all=[]

attrs_pred_max = 300

attrs_idx = list(range(df_z_all.shape[1]))

for r in range(1, df_z_all.shape[1]):
    # for cross-validation
    if r==df_z_all.shape[1]-1:
        folds = StratifiedKFold(n_splits=cvFolds, shuffle=True, random_state=myseed)
    else:
        folds = MultilabelStratifiedKFold(n_splits=cvFolds, shuffle=True, random_state=myseed)
    
    # MASS-selected attributes
    z=df_z_all.iloc[df_z_all.shape[0]-r,:].values
    x_idxs_MASS = [i for i, _ in enumerate(z) if _ == 1]
    y_idxs_MASS = [i for i, _ in enumerate(z) if _ == 0]

    # max-entropy-selected attributes
    x_idxs_ent = x_idxs_byentropy[:r]
    x_idxs_ent.sort()
    y_idxs_ent = list(set(attrs_idx) - set(x_idxs_ent))
    
    # draw random attributes
    if r == 1:
        attrs_remaining = list(set(attrs_idx) - set(x_idxs_MASS))
        idxs_rand = [([x], list(set(attrs_idx) - set([x]))) for x in attrs_remaining]
    else:
        idxs_rand = list(sample_attrs(attrs_idx, r, attrs_pred_max, myseed))

    # first list item is the MASS-selected attr set
    x_idxs = [x_idxs_MASS] + [x_idxs_ent] + [xx[0] for xx in idxs_rand]
    y_idxs = [y_idxs_MASS] + [y_idxs_ent] + [xx[1] for xx in idxs_rand]

    for i in range(len(x_idxs)):
        x_idx = x_idxs[i]
        y_idx = y_idxs[i]
        x_idx_short = '|'.join([str(x) for x in x_idx])

        y_split = X[:,y_idx]
        name_i = names_raw[y_idx]
    
        for fold_, (trn_idx, test_idx) in enumerate(folds.split(X,y_split)):        
            print('r, i, fold_, and x_idx==', r, i, fold_, x_idx_short, end=';  ')  
            train_X, test_X = X[trn_idx][:,x_idx], X[test_idx][:,x_idx]
            train_y, test_y = X[trn_idx][:,y_idx], X[test_idx][:,y_idx]
        
            if fold_==0:#,name_i
                print('train_y.shape, train_y/test_y.mean:',train_y.shape, round(train_y.mean(),2), round(test_y.mean(),2))
        
            y_te_pre = []
            for j in range(train_y.shape[1]):
                rfc=RandomForestClassifier(n_estimators=10, random_state=myseed,n_jobs=5,class_weight="balanced")
                rfc.fit(train_X, train_y[:,j])
                y_te_pre.append(rfc.predict(test_X))
            y_te_pre = np.array(y_te_pre).T
            tn_fp_fn_tp = confusion_matrix(test_y.ravel(), y_te_pre.ravel()).ravel()
            tn_fp_fn_tp = '|'.join( [str(x) for x in tn_fp_fn_tp] )
            
            stats_all.append([r, i, x_idx_short,fold_, tn_fp_fn_tp])
            acc_all.append([r, i, x_idx_short,fold_, accuracy_score(test_y.ravel(), y_te_pre.ravel())])
            b_acc_all.append([r, i, x_idx_short,fold_, balanced_accuracy_score(test_y.ravel(), y_te_pre.ravel())])
            f1_weight_all.append([r, i, x_idx_short,fold_, f1_score(test_y.ravel(), y_te_pre.ravel(), average='weighted')])
            jaccard_all.append([r, i, x_idx_short,fold_, jaccard_score(test_y.ravel(), y_te_pre.ravel(), average='weighted')])
            cohen_kappa_all.append([r, i, x_idx_short,fold_, cohen_kappa_score(test_y.ravel(), y_te_pre.ravel())])
            mcc_all.append([r, i, x_idx_short,fold_, matthews_corrcoef(test_y.ravel(), y_te_pre.ravel())])

r, i, fold_, and x_idx== 1 0 0 7;  train_y.shape, train_y/test_y.mean: (509, 45) -0.42 -0.42
r, i, fold_, and x_idx== 1 0 1 7;  r, i, fold_, and x_idx== 1 0 2 7;  r, i, fold_, and x_idx== 1 0 3 7;  r, i, fold_, and x_idx== 1 0 4 7;  r, i, fold_, and x_idx== 1 1 0 12;  train_y.shape, train_y/test_y.mean: (509, 45) -0.42 -0.41
r, i, fold_, and x_idx== 1 1 1 12;  r, i, fold_, and x_idx== 1 1 2 12;  r, i, fold_, and x_idx== 1 1 3 12;  r, i, fold_, and x_idx== 1 1 4 12;  r, i, fold_, and x_idx== 1 2 0 0;  train_y.shape, train_y/test_y.mean: (509, 45) -0.4 -0.39
r, i, fold_, and x_idx== 1 2 1 0;  r, i, fold_, and x_idx== 1 2 2 0;  r, i, fold_, and x_idx== 1 2 3 0;  r, i, fold_, and x_idx== 1 2 4 0;  r, i, fold_, and x_idx== 1 3 0 1;  train_y.shape, train_y/test_y.mean: (509, 45) -0.4 -0.4
r, i, fold_, and x_idx== 1 3 1 1;  r, i, fold_, and x_idx== 1 3 2 1;  r, i, fold_, and x_idx== 1 3 3 1;  r, i, fold_, and x_idx== 1 3 4 1;  r, i, fold_, and x_idx== 1 4 0 2;  train_y.shape, train_y/test_y.m

/Users/konrad/mambaforge/lib/python3.10/site-packages/sklearn/metrics/_classification.py:673: RuntimeWarning: invalid value encountered in scalar divide
  k = np.sum(w_mat * confusion) / np.sum(w_mat * expected)


r, i, fold_, and x_idx== 43 73 3 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|22|23|24|25|26|27|29|30|31|32|33|34|35|36|37|38|39|41|42|43|44|45;  r, i, fold_, and x_idx== 43 73 4 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|22|23|24|25|26|27|29|30|31|32|33|34|35|36|37|38|39|41|42|43|44|45;  r, i, fold_, and x_idx== 43 74 0 0|1|2|3|4|5|6|7|8|9|10|11|12|14|15|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|42|43|44|45;  train_y.shape, train_y/test_y.mean: (509, 3) 0.28 0.3
r, i, fold_, and x_idx== 43 74 1 0|1|2|3|4|5|6|7|8|9|10|11|12|14|15|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|42|43|44|45;  r, i, fold_, and x_idx== 43 74 2 0|1|2|3|4|5|6|7|8|9|10|11|12|14|15|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|42|43|44|45;  r, i, fold_, and x_idx== 43 74 3 0|1|2|3|4|5|6|7|8|9|10|11|12|14|15|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|42|43|44|45;  r, i, fold_, and x_idx

/Users/konrad/mambaforge/lib/python3.10/site-packages/sklearn/metrics/_classification.py:2184: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")


r, i, fold_, and x_idx== 44 189 0 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|25|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|42|43|44|45;  train_y.shape, train_y/test_y.mean: (509, 2) -0.46 -0.47
r, i, fold_, and x_idx== 44 189 1 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|25|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|42|43|44|45;  r, i, fold_, and x_idx== 44 189 2 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|25|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|42|43|44|45;  r, i, fold_, and x_idx== 44 189 3 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|25|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|42|43|44|45;  r, i, fold_, and x_idx== 44 189 4 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|25|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|42|43|44|45;  r, i, fold_, and x_idx== 44 190 0 0|1|2|4|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|41|42|43|4

...

r, i, fold_, and x_idx== 45 151 0 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|32|33|34|35|36|37|38|40|41|42|43|44|45;  train_y.shape, train_y/test_y.mean: (508, 1) -0.44 -0.44
r, i, fold_, and x_idx== 45 151 1 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|32|33|34|35|36|37|38|40|41|42|43|44|45;  r, i, fold_, and x_idx== 45 151 2 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|32|33|34|35|36|37|38|40|41|42|43|44|45;  r, i, fold_, and x_idx== 45 151 3 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|32|33|34|35|36|37|38|40|41|42|43|44|45;  r, i, fold_, and x_idx== 45 151 4 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|32|33|34|35|36|37|38|40|41|42|43|44|45;  r, i, fold_, and x_idx== 45 152 0 0|1|2|3|4|5|6|7|8|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|32|33|34|35|36|37|38

/Users/konrad/mambaforge/lib/python3.10/site-packages/sklearn/model_selection/_split.py:700: UserWarning: The least populated class in y has only 4 members, which is less than n_splits=5.
  warnings.warn(
/Users/konrad/mambaforge/lib/python3.10/site-packages/sklearn/metrics/_classification.py:673: RuntimeWarning: invalid value encountered in scalar divide
  k = np.sum(w_mat * confusion) / np.sum(w_mat * expected)


r, i, fold_, and x_idx== 45 220 0 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|41|42|43|44|45;  train_y.shape, train_y/test_y.mean: (508, 1) -0.43 -0.42
r, i, fold_, and x_idx== 45 220 1 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|41|42|43|44|45;  r, i, fold_, and x_idx== 45 220 2 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|41|42|43|44|45;  r, i, fold_, and x_idx== 45 220 3 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|41|42|43|44|45;  r, i, fold_, and x_idx== 45 220 4 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|26|27|28|29|30|31|32|33|34|35|36|37|38|39|40|41|42|43|44|45;  r, i, fold_, and x_idx== 45 221 0 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|19|20|21|22|23|24|25|26|27|28|29|30|31|32|33|34|35|36|37|38|

/Users/konrad/mambaforge/lib/python3.10/site-packages/sklearn/model_selection/_split.py:700: UserWarning: The least populated class in y has only 4 members, which is less than n_splits=5.
  warnings.warn(
/Users/konrad/mambaforge/lib/python3.10/site-packages/sklearn/metrics/_classification.py:673: RuntimeWarning: invalid value encountered in scalar divide
  k = np.sum(w_mat * confusion) / np.sum(w_mat * expected)


r, i, fold_, and x_idx== 45 248 0 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|33|34|35|36|37|38|39|40|41|42|43|44|45;  train_y.shape, train_y/test_y.mean: (508, 1) -0.99 -0.98
r, i, fold_, and x_idx== 45 248 1 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|33|34|35|36|37|38|39|40|41|42|43|44|45;  r, i, fold_, and x_idx== 45 248 2 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|33|34|35|36|37|38|39|40|41|42|43|44|45;  r, i, fold_, and x_idx== 45 248 3 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|33|34|35|36|37|38|39|40|41|42|43|44|45;  r, i, fold_, and x_idx== 45 248 4 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|33|34|35|36|37|38|39|40|41|42|43|44|45;  r, i, fold_, and x_idx== 45 249 0 0|1|2|3|4|5|6|7|8|9|10|11|12|13|14|15|16|17|18|19|20|21|22|23|24|25|26|27|28|29|30|31|32|33|34|36|37|38|

In [ ]:
# tn_fp_fn_tp = confusion_matrix(test_y.ravel()[:100],y_te_pre.ravel()[:100]).ravel()
# print( '|'.join( [str(x) for x in tn_fp_fn_tp] ) )

#tn, fp, fn, tp = tn_fp_fn_tp
#print( (tp+tn)/(tp+tn+fn+fp) )
#print( (tp+tn)/(tp+tn+fn+fp) )
#print( 0.5*((tp)/(tp+fn)+(tn)/(tn+fp)) )
#precision = tp/(tp+fp)
#recall = (tp)/(tp+fn)
#print( 2 * (precision * recall) / (precision + recall) )

In [15]:
pd.DataFrame.from_records(stats_all,
                          columns=['# of predictors', 'i', 'predictors', 'fold', 'tn|fp|fn|tp']).to_csv(
    f'../Results/MIP_bacdive1_baseline_20230523_stats-stats.csv', index=False)
pd.DataFrame.from_records(acc_all,
                          columns=['# of predictors', 'i', 'predictors', 'fold', 'accuracy']).to_csv(
    f'../Results/MIP_bacdive1_baseline_20230523_stats-acc.csv', index=False)
pd.DataFrame.from_records(b_acc_all,
                          columns=['# of predictors', 'i', 'predictors', 'fold', 'balanced_accuracy']).to_csv(
    f'../Results/MIP_bacdive1_baseline_20230523_stats-bacc.csv', index=False)
pd.DataFrame.from_records(f1_weight_all,
                          columns=['# of predictors', 'i', 'predictors', 'fold', 'f1_score_weighted']).to_csv(
    f'../Results/MIP_bacdive1_baseline_20230523_stats-f1weighted.csv', index=False)
pd.DataFrame.from_records(jaccard_all,
                          columns=['# of predictors', 'i', 'predictors', 'fold', 'jaccard_score']).to_csv(
    f'../Results/MIP_bacdive1_baseline_20230523_stats-jaccard.csv', index=False)
pd.DataFrame.from_records(cohen_kappa_all,
                          columns=['# of predictors', 'i', 'predictors', 'fold', 'cohen_kappa_score']).to_csv(
    f'../Results/MIP_bacdive1_baseline_20230523_stats-cohen_kappa.csv', index=False)
pd.DataFrame.from_records(mcc_all,
                          columns=['# of predictors', 'i', 'predictors', 'fold', 'mcc']).to_csv(
    f'../Results/MIP_bacdive1_baseline_20230523_stats-mcc.csv', index=False)